In [ ]:
!pip3 install nltk

In [149]:
import pandas as pd
import numpy as np
import re
import nltk
from collections import Counter
import string

In [150]:
shark_data = pd.read_csv('sharks.csv' )
# Primero debemos ver como esta constituido nuestra data.
df = pd.DataFrame(shark_data)
df.columns = ['Case Number','Date','Year','Type','Country','Area','Location',
       'Activity','Name','Sex','Age','Injury','Fatal_(Y/N)','Time',
       'Species','Investigator/Source','pdf','href_formula','href',
       'CaseNumber_1','CaseNumber_2','original_order','Unnamed:_22',
       'Unnamed:_23']

In [151]:
# Funciones básicas para columnas de tipo object

tamaño = range(len(df))
            
no_info = lambda element: 'no information' if element=='' or element =='nan' or element=='.' else element
            
def lower(colum_name):
    df[colum_name] = df[colum_name].apply(lambda i: str(i).lower())
    
esp_1 = lambda x: re.sub('^\s+', "", x)
esp_2 = lambda x: re.sub('\s$', "", x)
esp_3 = lambda x: re.sub('\s{2}', "", x)
esp_4 = lambda x: re.sub('\s\s$', "", x)

def espacios(colum_name):
    df[colum_name] = df[colum_name].apply(esp_1)
    df[colum_name] = df[colum_name].apply(esp_2)
    df[colum_name] = df[colum_name].apply(esp_3)
    df[colum_name] = df[colum_name].apply(esp_4)

par = lambda x: re.sub('\(\w*', "", x)    

def parentesis(colum_name):
    df[colum_name] = df[colum_name].str.replace("?","")
    df[colum_name] = df[colum_name].str.replace(")","")
    df[colum_name] = df[colum_name].apply(par)


between = lambda element:'no information' if 'between' in element else element

In [152]:
# .....DATE.....
lower('Date')
df.Date = df.Date.str.replace("reported","")
df.Date= df.Date.str.replace("before ","")
espacios('Date')
parentesis('Date')
df['Date'] = df['Date'].apply(between)
#set(df['Date'])

In [153]:
months ={'jan':'01',
         'feb':'02',
         'mar':'03',
         'apr':'04',
         'may':'05',
         'jun':'06',
         'jul':'07',
         'aug':'08',
         'sep':'09',
         'oct':'10', 
         'nov':'11',
         'dec':'12'}
def format_date(element):
    element = element.replace('-','/')
    for key in months:
        element = element.replace(key,months[key])
    return element

In [154]:
path1 = '\d{2}\/\d{2}\/\d{2}|\d{2}\-[aA-zZ]{3}\-\d{4}|\d{2}\-[aA-zZ]{3}\-\d{2}'
y = [re.findall(path1,df.Date[i]) for i in tamaño ]
dates = list(map((lambda x: "no information" if x == []  else format_date(x[0])), y))
df.Date = dates

In [155]:
# ---Year----
years = list(map((lambda i: i if len(str(i))== 4 else 'No information'),df['Year']))
df['Year']= years

In [156]:
# ----Sex----
lower('Sex')
df['Sex'] = df['Sex'].apply(no_info)
espacios('Sex')
sexo =lambda x: x if x =='m' or x=='f'  or x == 'no information' else 'no information'
df.Sex = df.Sex.apply(sexo)

In [157]:
# ----Fatal----
lower('Fatal_(Y/N)')
df['Fatal_(Y/N)'] = df['Fatal_(Y/N)'].apply(no_info)
espacios('Fatal_(Y/N)')
fatal =lambda x: x if x =='n' or x=='y'  or x == 'no information' else 'no information'
df['Fatal_(Y/N)'] = df['Fatal_(Y/N)'].apply(fatal)

In [158]:
#------pdf------
lower('pdf')
df['pdf'] = df['pdf'].apply(no_info)
espacios('pdf')
PDF=lambda x: x if x.endswith('.pdf') else 'no information'
df['pdf']=df['pdf'].apply(PDF)
#set(df['pdf']

In [159]:
#----href----
lower('href')
df['href'] = df['href'].apply(no_info)
espacios('href')
http = lambda x: x if x.startswith('http://') else 'no information'
df['href'] = df['href'].apply(http)

In [160]:
#----href_formula----
lower('href_formula')
df['href_formula']=df['href_formula'].apply(no_info)
espacios('href_formula')
df['href_formula'] = df['href_formula'].apply(http)

In [161]:
#----Unnamed:_22----
lower('Unnamed:_22')
df['Unnamed:_22']=df['Unnamed:_22'].apply(no_info)

In [162]:
#----Unnamed:_23----
lower('Unnamed:_23')
df['Unnamed:_23']=df['Unnamed:_23'].apply(no_info)

In [163]:
#----CaseNumber_1----
lower('CaseNumber_1')
path3 = '\d{4}\.\d{2}\.\d{2}\.\w+|\d{4}\.\d{2}\.\d{2}'
case = [re.findall(path3,df['CaseNumber_1'][i]) for i in tamaño]
case_1 = list(map((lambda x: "no information" if x == []  else x[0]),case))
df['CaseNumber_1'] = case_1

In [164]:
#----CaseNumber_2----
lower('CaseNumber_2')
case_ = [re.findall(path3,df['CaseNumber_2'][i]) for i in tamaño]
case_2 = list(map((lambda x: "no information" if x == []  else x[0]),case_))
df['CaseNumber_2'] = case_2

In [165]:
#----Location----
lower('Location')
df['Location'] = df['Location'].str.replace("off ","")
df['Location']=df['Location'].apply(no_info)
espacios('Location')

In [166]:
#----Time----
lower('Time')
df['Time'] = df['Time'].str.replace('before ',"")
df['Time'] = df['Time'].str.replace('early ',"")
df['Time'] = df['Time'].str.replace('-',"")
df['Time'] = df['Time'].str.replace('.',"")
df['Time'] = df['Time'].str.replace('>',"")
df['Time'] = df['Time'].str.replace('<',"")
df['Time'] = df['Time'].apply(no_info)
espacios('Time')
df['Time'] = df['Time'].apply(between)
df['Time'].value_counts()

no information                        3222
afternoon                              182
11h00                                  123
morning                                120
12h00                                  108
15h00                                  100
14h00                                   94
16h00                                   94
16h30                                   72
14h30                                   71
13h00                                   71
17h30                                   70
17h00                                   65
18h00                                   62
15h30                                   62
11h30                                   61
night                                   59
13h30                                   56
10h00                                   53
09h00                                   46
10h30                                   46
evening                                 33
12h30                                   33
late aftern

In [167]:
night = ['22','23','00','01','02','03','04','05','06']
morning = ['07','08','09','10','11']
afternoon = ['12','13','14','15','16','17']
evening = ['18','19','20','21']
    
def time(lista,nombre):
    for i in lista:
        df['Time'][df['Time'].str.startswith(i)]= nombre
            
time(night,'night')
time(morning,'morning')
time(afternoon,'afternoon')
time(evening,'evening')
df['Time'].value_counts()

/Users/valeriajimeno/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


no information                                                        3222
afternoon                                                             1441
morning                                                                808
evening                                                                236
night                                                                  140
late afternoon                                                          33
dusk                                                                    16
am                                                                      14
pm                                                                      12
midday                                                                  10
sunset                                                                   4
midnight                                                                 4
                                                                         4
just noon                

In [168]:
espacios('Time')
n = ['night','pm','dusk','dark','midnight']
m = ['morning','am']
a = ['afternoon','sunset','day','sundown','mid afternoon', 'late afternoon','midday']

def time2(lista,nombre):
    for i in lista:
        df['Time'][df['Time'].str.contains(pat = i)]=nombre

time(n,'night')
time(m,'morning')
time(a,'afternoon')

/Users/valeriajimeno/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [169]:
final_clea_t= lambda x: x if x=='no information' or x=='afternoon' or x=='morning' or x=='evening' else 'no information'
df['Time']=df['Time'].apply(final_clea_t)
df['Time'].value_counts()

no information    3442
afternoon         1492
morning            822
evening            236
Name: Time, dtype: int64

In [170]:
#----type----
#   ESPECÍFICO
df['Type'][df['Type'].str.startswith('Boat')]='Boating'

/Users/valeriajimeno/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()


In [171]:
#----Activity----
lower('Activity')
df['Activity']=df['Activity'].apply(no_info)
espacios('Activity')
parentesis('Activity')

In [172]:
##### nueva funcion para strings 
actv = df.Activity.values.tolist()
actv_s = [nltk.tokenize.wordpunct_tokenize(text) for text in actv]
stopwords = nltk.corpus.stopwords.words('english')

In [74]:
from itertools import groupby

def clear_multiple_char(comment):        
    ti = []
    for words in comment:
        t = [''.join(["".join(i) for i, _ in groupby(word)]) if len(word)>10 else word for word in words]
        ti.append(t)
    return ti

atv_ = clear_multiple_char(actv_s)

In [75]:
punctuation = string.punctuation # '!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'
punctuation += '0123456789'

def comment_raiz(comment):
    text = []
    for lista in comment:
        valids = [word for word in lista if word not in stopwords and word not in punctuation and len(word)>2]
        valids_true = [''.join([char for char in word if char not in punctuation]) for word in valids if 
                       len(''.join([char for char in word if char not in punctuation]))>0]
        text.append(valids_true)
    return text

lista_limpia=comment_raiz(atv_)# Add numbers

In [76]:
from nltk.corpus import wordnet as wn
from nltk.tokenize import word_tokenize, sent_tokenize 

lis_type = [nltk.pos_tag(lista_limpia[i])for i in range(len(lista_limpia))]

In [145]:
'''
from nltk.stem.lancaster import LancasterStemmer

stemmer = LancasterStemmer()
punctuation = string.punctuation # '!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'
punctuation += '0123456789'

def comment_raiz(comment):
    text = []
    for lista in comment:
        valids = [stemmer.stem(word) for word in lista if word not in stopwords and word not in punctuation and len(word)>2]
        valids_true = [''.join([char for char in word if char not in punctuation]) for word in valids if 
                       len(''.join([char for char in word if char not in punctuation]))>0]
        text.append(valids_true)
    return text

atv_fin=comment_raiz(atv_)# Add numbers

atv_fin




from nltk.corpus import wordnet as wn
from nltk.tokenize import word_tokenize, sent_tokenize 

w_vb = list(map((lambda lista: nltk.pos_tag(lista[i][0]) for i in range(len(pruebita))),listilla))
lista = []

for i in range(len(pruebita)):
    tagged = nltk.pos_tag(lista[i][0])
    lista.append(tagged)
'''

'\nfrom nltk.stem.lancaster import LancasterStemmer\n\nstemmer = LancasterStemmer()\npunctuation = string.punctuation # \'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~\'\npunctuation += \'0123456789\'\n\ndef comment_raiz(comment):\n    text = []\n    for lista in comment:\n        valids = [stemmer.stem(word) for word in lista if word not in stopwords and word not in punctuation and len(word)>2]\n        valids_true = [\'\'.join([char for char in word if char not in punctuation]) for word in valids if \n                       len(\'\'.join([char for char in word if char not in punctuation]))>0]\n        text.append(valids_true)\n    return text\n\natv_fin=comment_raiz(atv_)# Add numbers\n\natv_fin\n\n\n\n\nfrom nltk.corpus import wordnet as wn\nfrom nltk.tokenize import word_tokenize, sent_tokenize \n\nw_vb = list(map((lambda lista: nltk.pos_tag(lista[i][0]) for i in range(len(pruebita))),listilla))\nlista = []\n\nfor i in range(len(pruebita)):\n    tagged = nltk.pos_tag(lista[i][0])\n    lista.a

In [77]:
def counter(comment_clear):
    cnt = Counter()
    for words in comment_clear:
        for word in words:
            cnt[word] += 1
    return cnt
#atv_cnt = counter(atv_fin) 

from nltk.corpus import wordnet as wn

dic_limpio = dict(counter(lista_limpia))
activities = list(filter((lambda key: key.endswith('ing')),dic_limpio))
activities

['surfing',
 'fishing',
 'wading',
 'swimming',
 'boarding',
 'spearfishing',
 'snorkeling',
 'kayaking',
 'lobstering',
 'diving',
 'floating',
 'standing',
 'teasing',
 'skiing',
 'walking',
 'feeding',
 'windsurfing',
 'photographing',
 'padleboarding',
 'treading',
 'playing',
 'attempting',
 'sitting',
 'rowing',
 'bodysurfing',
 'filming',
 'falling',
 'canoeing',
 'petting',
 'kneeling',
 'tagging',
 'watching',
 'culling',
 'kitesurfing',
 'sailing',
 'kiteboarding',
 'casting',
 'wrangling',
 'cleaning',
 'dragging',
 'bathing',
 'bodyboarding',
 'crayfishing',
 'jumping',
 'collecting',
 'washing',
 'holding',
 'wakeboarding',
 'rescuing',
 'measuring',
 'paddling',
 'drowning',
 'crawling',
 'crabbing',
 'sinking',
 'towing',
 'removing',
 'observing',
 'reviving',
 'shrimping',
 'modeling',
 'kissing',
 'lifesaving',
 'touching',
 'competing',
 'crouching',
 'scurfing',
 'chumming',
 'carrying',
 'poaching',
 'boeing',
 'wearing',
 'hiking',
 'whiting',
 'conducting',
 'kil

In [189]:
df.Activity

0                                                 surfing
1                                                 surfing
2                                                 surfing
3                                                 surfing
4                                                 surfing
5                                                 fishing
6                                                  wading
7                                                swimming
8                                            kite surfing
9                                         boogie boarding
10                                                surfing
11                                          body boarding
12                                           spearfishing
13                                                surfing
14                                                surfing
15                                                surfing
16                                                 wading
17            

In [79]:
for i in activities:
    df['Activity'][df['Activity'].str.contains(pat = i)]=i

/Users/valeriajimeno/anaconda/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


In [81]:
def act(s):
    activities = list(filter((lambda key: key.endswith('ing')),dic_limpio))
    for i in activities:
        if i in s:
            s = i
        else:
            s = 'no information'
    return s

prueba = list(map(act,df.Activity))




True

In [193]:
fun = lambda x: for i in activities if i in x else 'no information'
df['Activity'] = df['Activity'].apply(fun)
df['Activity']

SyntaxError: invalid syntax (<ipython-input-193-97e21d5acd60>, line 1)

In [185]:
def actv():
    pru = []
    activities = list(filter((lambda key: key.endswith('ing')),dic_limpio))
    for i in activities:
        pru.append(list(map((lambda element: i if i in element else 'no information' ),df.Activity)))
    #info_no = list(map((lambda x: ['no information'] if x ==[] else x),pru))
    #b = [y for x in pru for y in x]
    print(pru)

actv()


[['surfing', 'surfing', 'surfing', 'surfing', 'surfing', 'no', 'no', 'no', 'surfing', 'no', 'surfing', 'no', 'no', 'surfing', 'surfing', 'surfing', 'no', 'no', 'no', 'surfing', 'no', 'no', 'no', 'no', 'surfing', 'surfing', 'surfing', 'no', 'no', 'no', 'surfing', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'surfing', 'no', 'no', 'no', 'no', 'surfing', 'no', 'no', 'no', 'surfing', 'no', 'no', 'no', 'no', 'surfing', 'surfing', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'surfing', 'surfing', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'no', 'surfing', 'no', 'surfing', 'no', 'surfing', 'surfing', 'no', 'no', 'no', 'no', 'surfing', 'no', 'no', 'no', 'surfing', 'no', 'surfing', 'no', 'surfing', 'surfing', 'no', 'no', 'no', 'surfing', 'no', 'no', 'no', 'no', 'no', 'surfing', 'no', 'no', 'no', 'no', 'no', 'surfing', 'no', 'surfing', 'surfing', 'surfing', 'no', 'no', 'no', 'no', 'no', 'surfing', 'surfing', 'surfing', 'no', 'surfing', 'no', 'no', 'no', 'surfing', 'n

In [ ]:
# Particular
def activ(s):
    for i in activities:
    if "fishing" in s:
        s = "fishing"
    elif 'floating' in s:
        s = 'floating'
    elif 'surfing' in s:
        s = 'surfing'
    elif 'diving' in s:
        s = 'diving'
    elif 'swimming' in s:
        s = 'swimming'
    elif 'playing' in s:
        s = 'playing'
    elif 'boating' in s:
        s = 'boating'
    elif 'pulling' in s:
        s = 'pulling'
    elif 'walking' in s:
        s = 'walking'
    elif 'hauling' in s:
        s = 'hauling'
    elif 'hiking' in s:
        s = 'hiking'
    elif 'lying' in s:
        s = 'lying'
    elif 'padling' in s:
        s = 'padling'
    elif 'photographing' in s:
        s = 'photographing'
    elif 'washing' in s:
        s = 'washing'
    elif 'wading' in s:
        s = 'wading'
    elif 'working' in s:
        s = 'working'
    elif 'cleaning' in s:
        s = 'cleaning'
    elif 'collecting' in s:
        s = 'collecting'
    elif 'hunting' in s:
        s = 'hunting'
    elif 'snorkeling' in s:
        s = 'hunting'
    elif 'splashing' in s:
        s = 'splashing'
    elif 'spearing' in s:
        s = 'spearing'
    elif 'snorkeling' in s:
        s = 'standing'
    elif 'testing' in s:
        s = 'testing'
    elif 'trailing' in s:
        s = 'trailing'
    elif 'treading' in s:
        s = 'treading'
    elif 'feeding' in s:
        s = 'feeding animals'
    elif 'fell' in s:
        s = 'fell of'
    elif 'feeding' in s:
        s = 'feeding'
    elif 'filming' in s:
        s = 'filming'
    elif 'gathering' in s:
        s = 'gathering'
    elif 'gaffing' in s:
        s = 'gaffing'
    elif 'kayaking' in s:
        s = 'kayaking'
    elif 'killing' in s:
        s = 'killing'
    elif 'jumping' in s:
        s = 'jumping'
    elif 'adrift' in s:
        s = 'adrift'
    elif 'air disaster' in s or "aircraft" in s:
        s = 'air disaster'
    elif 'rescue' in s or 'rescuing' in s:
        s = 'rescuing'
    elif 'sitting' in s:
        s = 'nsitting'
    elif 'sinking' in s:
        s = 'sinking'
    elif 'sea disaster' in s:
        s = 'sea disaster'
    elif 'removing' in s:
        s = 'removing animals from trap'
    elif 'paddling' in s:
        s = 'paddling'
    elif 'bathing' in s:
        s = 'bathing'
    elif 'standing' in s:
        s = 'standing'
  
    return s   
    
df['Activity']=df['Activity'].apply(activ)    
set(df['Activity'])

In [147]:
lower('Country')
df['Country']=df['Country'].apply(no_info)
espacios('Country')
parentesis('Country')

In [ ]:
#     específico
for i  in range(len(df)):
    if 'ocean' in df['Country'][i] or 'sea' in df['Country'][i] or 'gulf' in df['Country'][i] or 'golf' in df['Country'][i] or 'diego garcia' in df['Country'][i] or '/' in df['Country'][i]:
        df['Country'][i] = 'no information'

In [ ]:
df['Country'] = df['Country'].str.replace("st. maartin","st. martin")
#set(df.Country)

In [148]:
# Area

lower('Area')
df['Area']=df['Area'].apply(no_info)
espacios('Area')
parentesis('Area')
coma = lambda x: re.sub('\,[a-z]|\,\s[a-z]*', "", x)
df['Area'] = df['Area'].apply(coma)

In [ ]:
num = list(range(10))
def numbr (column_name):
    for i in num:
        for j in tamaño:
            if str(i) in df[column_name][j]:
                df[column_name][j] = 'no information'
            
numbr('Area')
#set(df.Area)

In [176]:
#ANALISIS

df.describe(include=[object])

Case Number            Date  Year        Type Country     Area  \
count           5992            5992  5992        5992    5949     5590   
unique          5976            4489   229           5     203      785   
top     1907.10.16.R  no information  2015  Unprovoked     USA  Florida   
freq               2             889   139        4386    2116      990   

              Location Activity  Name   Sex       ...                  Time  \
count             5992     5992  5792  5992       ...                  5992   
unique            3856     1422  5009     3       ...                     4   
top     no information  surfing  male     m       ...        no information   
freq               496      907   495  4837       ...                  3442   

            Species Investigator/Source             pdf    href_formula  \
count          3058                5977            5992            5992   
unique         1538                4752            5955            5979   
top     White shark      C. Moore, GSAF  no information  no information   
freq            161                  94              27               3   

                  href    CaseNumber_1    CaseNumber_2     Unnamed:_22  \
count             5992            5992            5992            5992   
unique            5971            5847            5849               2   
top     no information  no information  no information  no information   
freq                 5             126             125            5991   

           Unnamed:_23  
count             5992  
unique               3  
top     no information  
freq              5990  

[4 rows x 23 columns]

In [ ]:
'''
El año con mas ataques de tiburon fue en el 2015, con 4386 ataques. Por otro lado
Florida, Estados Unidos, fue el área con mayor númoer de ataques de tiburon,
'''

In [181]:
pd.crosstab(df.Activity, df.Year)[[2015]]

Year                                                2015
Activity                                                
                                                       0
"boat accident"                                        0
"climbing up to ship after repairing the stern ...     0
"crossing the river"                                   0
"flying tiger" transport plane went down with 5...     0
"riding waves on a board"                              0
"swimming vigorously"                                  0
12 of the penang's crew were returning to the s...     0
13 men in the water after sailboat capsized & sank     0
14 m prawn trawler new venture capsized& sank i...     0
1446-ton norwegian barque errol, bound from per...     0
16' catamaran capsized previous night, occupant...     0
17 maldivians adrift in open boat for 31 days          0
2 messboys  & tony latona  were playing on the ...     0
25-foot cabin cruiser happy jack sank in heavy ...     0
3 men & 2 boys picked up wearing life jackets a...     0
3,909-ton panamanian freighter chieh lee sank i...     0
3-masted steel barque glenbank foundered during...     0
3.3 m fishing boat sank. treveluwe & peter hodg...     0
4 men were bathing                                     0
40' fishing boat sank                                  0
43-ton schooner irene capsized & sank                  0
63' fishing boat sno' bay foundered                    0
90 european civilians, many women & children, w...     0
a 210-ton brig was sunk by a japanese submarine...     0
a 75-tonjapanese fishing ship was sunk bychines...     0
a barque wrecked                                       0
a canoe was pursuing a schooner that had forcib...     0
a corsair's boat was overturned                        0
a dhow capsized                                        0
...                                                  ...
whena deckhandjumped overboard, mciver dived af...     0
wind surfing                                           0
windsurfing                                            0
windsurfing  on his board                              0
windsurfing, but sitting on his board                  0
wooden fishing boat                                    0
working near fish traps                                0
working on the bridge when he fell into the river      0
working prawn net                                      0
wrangling a shark                                      0
wreck / technical diving                               0
wreck of the 1308-ton norwegian ship auckland          0
wreck of the 150-ton brig maria                        0
wreck of the 1689-ton portuguesecoaster angoche        0
wreck of the schooner driver                           0
wreck of the schooner pohoiki                          0
wreck of the sovereign                                 0
wreck of the state oil company ship permina            0
wreck of the steamship birkenhead                      0
wreck of the steamship sultan of bombay                0
wreck of the tug magellan                              0
wreck of the union steamship company 982-ton ir...     0
wreck of the uss somers                                0
wreck oflarge double sailing canoe                     0
yacht gooney bird foundered, 4 survivors on raft       0
yacht of michael howell capsized                       0
yacht race                                             0
yachting accident                                      0
yachtsman in a zodiac                                  0
zosimo & his son, jeffrey popa, failed to retur...     0

[1422 rows x 1 columns]

In [186]:
df.groupby('Activity').agg(['mean', 'min', 'max'])

original_order            
                                                             mean   min   max
Activity                                                                     
                                                           2190.0   672  3708
"boat accident"                                             596.0   596   596
"climbing up to ship after repairing the stern ...         2079.0  2079  2079
"crossing the river"                                        595.0   595   595
"flying tiger" transport plane went down with 5...         1940.5  1940  1941
"riding waves on a board"                                  3858.0  3858  3858
"swimming vigorously"                                       957.0   957   957
12 of the penang's crew were returning to the s...         1363.0  1363  1363
13 men in the water after sailboat capsized & sank          636.0   636   636
14 m prawn trawler new venture capsized& sank i...         3289.0  3289  3289
1446-ton norwegian barque errol, bound from per...          809.0   809   809
16' catamaran capsized previous night, occupant...         3200.0  3200  3200
17 maldivians adrift in open boat for 31 days              2177.0  2177  2177
2 messboys  & tony latona  were playing on the ...         1688.0  1688  1688
25-foot cabin cruiser happy jack sank in heavy ...         2396.0  2396  2396
3 men & 2 boys picked up wearing life jackets a...         2020.0  2020  2020
3,909-ton panamanian freighter chieh lee sank i...         3047.0  3047  3047
3-masted steel barque glenbank foundered during...          836.0   836   836
3.3 m fishing boat sank. treveluwe & peter hodg...         2964.0  2964  2964
4 men were bathing                                           17.0    17    17
40' fishing boat sank                                      3074.0  3074  3074
43-ton schooner irene capsized & sank                       277.0   277   277
63' fishing boat sno' bay foundered                        2473.0  2473  2473
90 european civilians, many women & children, w...         1598.0  1598  1598
a 210-ton brig was sunk by a japanese submarine...         1511.0  1511  1511
a 75-tonjapanese fishing ship was sunk bychines...         1709.0  1709  1709
a barque wrecked                                            569.0   569   569
a canoe was pursuing a schooner that had forcib...          552.0   552   552
a corsair's boat was overturned                             161.0   161   161
a dhow capsized                                             101.0   101   101
...                                                           ...   ...   ...
whena deckhandjumped overboard, mciver dived af...         2427.0  2427  2427
wind surfing                                               3821.0  3821  3821
windsurfing                                                3941.5  3248  5900
windsurfing  on his board                                  3538.0  3538  3538
windsurfing, but sitting on his board                      4195.0  4195  4195
wooden fishing boat                                          29.0    29    29
working near fish traps                                    1227.0  1227  1227
working on the bridge when he fell into the river           514.0   514   514
working prawn net                                          2108.0  2108  2108
wrangling a shark                                          5580.0  5580  5580
wreck / technical diving                                   4317.0  4317  4317
wreck of the 1308-ton norwegian ship auckland               805.0   805   805
wreck of the 150-ton brig maria                             349.0   349   349
wreck of the 1689-ton portuguesecoaster angoche            2850.0  2850  2850
wreck of the schooner driver                                187.0   187   187
wreck of the schooner pohoiki                               470.0   469   471
wreck of the sovereign                                      227.0   227   227
wreck of the state oil company ship permina                2631.0  2631  

In [187]:
df.isnull().sum()

Case Number               0
Date                      0
Year                      0
Type                      0
Country                  43
Area                    402
Location                  0
Activity                  0
Name                    200
Sex                       0
Age                    2681
Injury                   27
Fatal_(Y/N)               0
Time                      0
Species                2934
Investigator/Source      15
pdf                       0
href_formula              0
href                      0
CaseNumber_1              0
CaseNumber_2              0
original_order            0
Unnamed:_22               0
Unnamed:_23               0
dtype: int64

In [216]:
dna = 'AAA'
def dna(dna):
    t = []
    for i in dna.upper():
        if i == 'A':
            t.append('T')
        elif i == 'T':
            t.append('A')
        elif i == 'C':
            t.append('G')
        elif i == 'G':
            t.append('C')
    return ''.join(t)
dna('TTA')

'AAT'

In [210]:



def dna(dna):
    for i in dna.upper():
        print(i)
dna('TTA')

T
T
A


In [211]:
l = map((,dna.upper())

SyntaxError: invalid syntax (<ipython-input-211-0d0f3ede8f96>, line 1)